__Lab 01 - Acquisition__

Student Names: Ganesh Veluru and Jwala Sri Hari Badam

Group Number: 3

# Setup

## FPGA Cofigurations & Import Python Libraries

These are the FPGA configurations need when programming it with the bitstream.

BITSTREAM_FILENAME is the path and filename to the Bitstream to program the FPGA with.

Also, we import the Python libraries here.

In [111]:
import numpy as np
import serial
import serial.tools.list_ports
from tqdm import tnrange

DEVICE_NAME = "CmodS7"
DEVICE_ID   = 0
#BITSTREAM_FILENAME = "../Hardware/APUF_CmodS7_01.bit" # For both undergrad & grad students

BITSTREAM_FILENAME = "../Hardware/APUF_CmodS7_02.bit" # For grad students only

print("✔️ OK to continue!")

✔️ OK to continue!


## Connect to FPGA

We need to make sure the FPGA is connected.

"%%bash" indicated that the following code in that cell will run with "bash" instead of python.

In [112]:
!djtgcfg enum

print("✔️ OK to continue!")

Found 1 device(s)

Device: CmodS7
    Device Transport Type: 00020001 (USB)
    Product Name:          Digilent Cmod S7
    User Name:             CmodS7
    Serial Number:         210376AFE198
✔️ OK to continue!


Make sure to that it says "Found 1 device(s)" (or more) and the device name match with "DEVICE_NAME" from section 1.1

Also, we can verify the device ID (DEVICE_ID) from section 1.1 with the following code.

(DEVICE_ID should be 0 for CmodS7, unless you have other FPGA connected)

In [113]:
%%bash -s "$DEVICE_NAME"
djtgcfg init -d $1

Initializing scan chain...
Found Device ID: 037c4093

Found 1 device(s):
    Device 0: XC7S25


The actual device ID is located in the list at the bottom. It should say, for example:

<span class="mark">Found 1 device(s):</span> <br>
<pre> <span class="mark">Device 0: XC7S25</span>

The 0 here is the Device ID for "XC7S25" (i.e., CmodS7).

## Program the FPGA

Program the FPGA with the bitstream.

Also, make sure the BITSTREAM_FILENAME in section 1.1 matches with bitstream you want to programm the FPGA with.

In [114]:
%%bash -s "$DEVICE_NAME" "$DEVICE_ID" "$BITSTREAM_FILENAME"
djtgcfg prog -d $1 -i $2 -f $3

Programming device. Do not touch your board. This may take a few minutes...
Programming succeeded.


## Setup the USB serial communication port

Now, we can setup PySerial.

First, let's identify the USB port name where the FPGA is connected to. Use the function below to print a list of all your ports.

In [115]:
def print_ports():
    portsList = serial.tools.list_ports.comports()

    print("--- PORTS LIST ---")
    for p in sorted(portsList):
        # first prints the port, then the device product
        print(f'{p[0]} : {p[1]}')

print_ports()

print("✔️ OK to continue!")

--- PORTS LIST ---
/dev/ttyUSB3 : Digilent Adept USB Device - Digilent Adept USB Device
✔️ OK to continue!


In [116]:
# connect to COM port, set baudrate
port = "/dev/ttyUSB3"
boudrate = 115200
ser = serial.Serial(port, boudrate)

print("✔️ OK to continue!")

✔️ OK to continue!


load data from npz file, loads as directory with one item 'challenge'

In [117]:
#in_filename = "../Challenges/challenges_05k.npz" # for testing only
#in_filename = "../Challenges/challenges_10k.npz"
in_filename = "../Challenges/challenges_50k.npz" # final results must use this

data = np.load(in_filename)
challenges = data['challenge']
print((challenges))

print("✔️ OK to continue!")

['503e1f07e2049a5d' '9359431e8aa85425' '417cc562112bd099' ...
 '8c409f3fe2256e76' 'd813d0cf4621540b' 'cf35249a1fffca8a']
✔️ OK to continue!


# Send & Collect Data

Let's make a functions that will send 1 challenge and receive 1 response

__Complete missing parts__

In [118]:
# Function: get_1resp()
#   Input: 'ser' - serial connection to FPGA
#   Input: 'in_hex' - an input hex string to send to the FPGA
#   Input: 'resp_size' - size of the output response in bytes
#   Output: 'r_bin' - respective binary string response of size 'resp_size' bytes (8*resp_size bits).


def get_1resp(ser: serial.Serial, in_hex: str, resp_size: int) -> str:


    # convert hex string to bytearray
    in_bytes = bytearray.fromhex(in_hex)
    print(in_bytes)

    # send bytes to FPGA
    ser.write(in_bytes)
    

    # get response: reads n bytes from FPGA (remember: 1 byte = 8 bits)
    r_bytes = ser.read(resp_size)
    print(r_bytes)
    # convert bytearray to int
    r_int = int.from_bytes(r_bytes, byteorder='big')
    print(r_int)
    # convert int to resp_size*8 bits binary string
    r_bin = format(r_int, "0"+str(8*resp_size)+"b")
    
    return r_bin

#print(get_1resp(ser))
print("✔️ OK to continue!")

✔️ OK to continue!


Test this function. Send an example challenge and return that value. The response size is 2 bytes.

In [119]:
# Example usage:
# Replace "/dev/ttyUSB1" with the correct COM port name, and 115200 with the desired baud rate

response = get_1resp(ser, str(data['challenge'][0]), 2)  # Example: sending "1A2B3C" hex and expecting a 2-byte response
# print("Response:", response)
# ser.close()  # Close the serial connection when done

bytearray(b'P>\x1f\x07\xe2\x04\x9a]')
b'\xbe\xec'
48876


Now, lets place this function in a loop to iterate all the challenges and get all the responses.

note: tnrange() is a fancy way to do loops. This is similar to range() function but makes a progress bar. It is nice to use when loading a lot of data.

__Complete missing parts__

In [120]:
# Function: get_all_resp()
#   Input: 'challanges' - NumPy array of challanges to send to the FPGA
#   Input: 'resp_size' - size of each output response in bytes
#   Output: 'responses' - NumPy array respective binary string response of size 'resp_size' bytes.

def get_all_resp(challenges: np.ndarray, resp_size: int):
    # initialize an empty list (or NumpPy array)
    L=[]
    
    # iterate through each challenge and get respective response
    N = len(challenges)
    for i in tnrange(N , desc='Generating APUF Responses'):
        L.append(get_1resp(ser,challenges[i],2))
        # do something
    
    #print(type(L))
    # If you used a list, convert responses to Numpy Array
    responses=np.array(L)
    # return your NumPy array of responses
    return responses

Now we can generate the responses

In [121]:
responses = get_all_resp(challenges, 2)

print("✔️ OK to continue!")


/tmp/ipykernel_3675/3816777311.py:12: TqdmDeprecationWarning: Please use `tqdm.notebook.trange` instead of `tqdm.tnrange`
  for i in tnrange(N , desc='Generating APUF Responses'):


Generating APUF Responses:   0%|          | 0/50000 [00:00<?, ?it/s]

bytearray(b'P>\x1f\x07\xe2\x04\x9a]')
b'\xfe\xe4'
65252
bytearray(b'\x93YC\x1e\x8a\xa8T%')
b'Zx'
23160
bytearray(b'A|\xc5b\x11+\xd0\x99')
b'\xe9\x9c'
59804
bytearray(b'\xe3\xfe|y\x15\xe0Y\x89')
b':\xde'
15070
bytearray(b'\xd2(\xc3\x19\xb3\x9cQ\x9d')
b'\xef\xff'
61439
bytearray(b'j.\xd0^\xe0\xd2\xf8Y')
b'\xfa\xc6'
64198
bytearray(b'_x\x8d;)7ye')
b'A\xbe'
16830
bytearray(b'\xb9\x9aCN\x16\xb4\xdea')
b'\x037'
823
bytearray(b'\xde\xa7&$F\xf0\xef\x05')
b'\x04;'
1083
bytearray(b'\xce\x8b\x03\xa3\xdc\xec\xe9\xa6')
b'\x1e\xac'
7852
bytearray(b'\x04\x9dO\xd9jC2\xf4')
b'\xff\x00'
65280
bytearray(b'\x9c|*"\xb1zg6')
b'\xf5\xb6'
62902
bytearray(b'\x0eP]v\xa6\x1b\xd8X')
b'\x08C'
2115
bytearray(b'\xb3d\xad\x1bC"\xd4\xa3')
b'\xa3\xfd'
41981
bytearray(b'\xa3{\xc6\x88\xab\x1e}N')
b'\xbd\xfc'
48636
bytearray(b'\xe0e\x9b\x0c\x11\xed\xcdu')
b'\xf7\xff'
63487
bytearray(b'\xb6VM/\x87D\x97G')
b'Dd'
17508
bytearray(b'\x07_I/\xd7\xf3\xb45')
b'y\x00'
30976
bytearray(b'\xe2B\xaeuN\xc6\xb6\xc9')
b'\xe3o'
58223
byte

b'\xff\xbe'
65470
bytearray(b'j\xb0JB\xce\x1a\x0fz')
b'\xff\x00'
65280
bytearray(b'\xab\xf4M\xbb\x8e\xcc\xbc\x07')
b'-4'
11572
bytearray(b'\xc0G@\x15\t\xbf\xe6z')
b'\xab\xbf'
43967
bytearray(b'g\xbd\x12w\x0f\xf6\xf4\x0e')
b'\xf7\xed'
63469
bytearray(b'\x15hc\xd9\xc5\x8e\x87\t')
b'\xb2^'
45662
bytearray(b'2\xca\xb5\xd1iIkZ')
b'\xff\xc4'
65476
bytearray(b'\x0b\x0f\x82\xa1:h\xafM')
b'(\xc2'
10434
bytearray(b'Q}\xa1\xc4ym\xa0z')
b'\xff\xb4'
65460
bytearray(b'\x9e\x9f\xbd\xc2\xaf\xe8\x94\xd2')
b'\xfb\xe6'
64486
bytearray(b'\x88.\x11\xed\x0f\xfa\x87\xea')
b' \x94'
8340
bytearray(b'\x8a\x15!\x7f\r\xd6\xcc\x0f')
b'u\xc2'
30146
bytearray(b'A\xc0\xca\xfe\xbc\xaf\xb7f')
b'\xef\xff'
61439
bytearray(b'\xa9E\xf8Do\xe8\xfe"')
b'\xfb\x00'
64256
bytearray(b'Q\xa2\xb5\x1e\x18\xe8l<')
b'}\xee'
32238
bytearray(b"\x85\'\xfe\xdfU\xf7t:")
b'\x00\x03'
3
bytearray(b'k\xe8\xf9\xe4\xd1\xa9\xf2*')
b'\x00\x01'
1
bytearray(b'\x11\xcf\xd4\xd5\x84\xc8\xd6\x12')
b'u('
29992
bytearray(b'Iy\x1cV\xa2\xbb\x1bo')
b'\xa9\x0

bytearray(b'\x86\xe2\x92ABg\xdc,')
b'\xd1\xc8'
53704
bytearray(b'\x0bw\xadG92n\xc2')
b'\xa4\xe4'
42212
bytearray(b'sLG\x05\xac`\xb3\xaa')
b'\xb1N'
45390
bytearray(b'a\xe4\xc8B\xe6b\x10\xf8')
b'o\xcf'
28623
bytearray(b'\xaa\x00\xc2\xf5H{\x93e')
b'\x06H'
1608
bytearray(b"z\'$\xd5\x8bk\xec\xb7")
b'q\xab'
29099
bytearray(b'\xd7EG!\xbe\xf6\r\x0b')
b'\xbe\xfd'
48893
bytearray(b'TF\xb7 \x0e-\x88D')
b'\xdd\xec'
56812
bytearray(b'%L\xcb\x8aH\xe7\x1dG')
b'\xf75'
63285
bytearray(b'\x9a\xfb\xc5.\x96\x03\x97\x1d')
b'\xc6\xff'
50943
bytearray(b'?[\xf6%\x0c\xd6\x14=')
b'\n\xe1'
2785
bytearray(b'\xc5\x05y\x85\x7f\xda\xef\xe6')
b'\x03$'
804
bytearray(b'`\x98U\xd2Z-.\xd7')
b',F'
11334
bytearray(b'\xc8e\x83\xba\x1c@\xdfW')
b'\xff\xbe'
65470
bytearray(b'rnD\x84Z-4\x86')
b'\xa2\xf6'
41718
bytearray(b'\xe7o{\xee\xad\xd2]1')
b'j\x1d'
27165
bytearray(b'\x1e\xf9cE\xc5\x9c\x0c\xba')
b'\xd7\xe8'
55272
bytearray(b'}\x169\xec\x7f\x98\xb0z')
b'\x00\x04'
4
bytearray(b'Q\x0f\xc7\x1bH\x83\x02w')
b';\x00'
15104
bytearr

...

b'\r\x1a'
3354
bytearray(b'*\x14\xf9\xc0\x19~?\x83')
b'm\xfa'
28154
bytearray(b'\x7f!\xb5\x82o\x956\x0b')
b'\xffg'
65383
bytearray(b'\xe1\xccy8\xa2J\x04\xc5')
b'\xdd\xf8'
56824
bytearray(b'kc"\x95\x05\xa1\xae\xf2')
b'\x18D'
6212
bytearray(b'\x0c\x1eu\x12Wb9\xd2')
b'\xf5\xf2'
62962
bytearray(b'\xaeA\xbf\xd3\xf7\xe4\xa2\x17')
b'\xff\x00'
65280
bytearray(b'%<C\x01\x1c`\x92\xbb')
b'q\xf2'
29170
bytearray(b'h\xd7b\xed\xc1\x11\x8d?')
b'p%'
28709
bytearray(b'\xd4\xa6@(\x97\xf5\x18\xfa')
b'Ww'
22391
bytearray(b'\x86K\xdd\xef\x07r\x8d\xa9')
b'\xc3^'
50014
bytearray(b'\x15@\x8d\xad\xba\x9c\x1a\xee')
b'\xaf\xb7'
44983
bytearray(b'\r\xed\xaa\xa8\x18 V*')
b'*\xab'
10923
bytearray(b'\xdc\xd3\r\xecsW\xbf\xd8')
b'Q\xc4'
20932
bytearray(b'\x89\xf1/*\xf6a\x1c\x8e')
b'~\xff'
32511
bytearray(b'\xac\xe6\xedp*\x05\xd4\x9f')
b'\x10\x1b'
4123
bytearray(b'\xb7\xb3\x8bO_\xb0\xfeq')
b'\xe5_'
58719
bytearray(b'\xce\xa2\r_\n\x04HE')
b'~p'
32368
bytearray(b'&\xbfa\xd7\x838)\xb8')
b'\xf3\xf2'
62450
bytearray(b'\xfe\

b'\xedp'
60784
bytearray(b'\xef\xb0u2\xbe\xe0\xd0\xc6')
b'\xa1F'
41286
bytearray(b'\xec?\x17[\xa1B\xfcC')
b'r\xd8'
29400
bytearray(b'\x0e\xca2\x14\x90Nt\x1c')
b'\x83\xe6'
33766
bytearray(b'\xee\x14p\xab]\x9a\x03\xae')
b'\xec\x04'
60420
bytearray(b'\xe3\xb0?5y_YZ')
b'\xc5\xe0'
50656
bytearray(b'\xd0Cm,\xb5\xfacz')
b'K\xf8'
19448
bytearray(b'\x9b\xe2\x12\xd5\xd4\t\xf0\x9f')
b'v\xf8'
30456
bytearray(b'\xfe\xfd\x14\x01[;\xd7\x96')
b'\xf5\x8e'
62862
bytearray(b'\xaf\x05\xa5Yy\xb5\x16j')
b'\xd3\x00'
54016
bytearray(b'\xc9h\xb1\xf4\xcaX\x90\x9f')
b'\xaf\x0b'
44811
bytearray(b'\x0co8\xed\x7f\xe8\xe7\x87')
b'\x7f\xf8'
32760
bytearray(b'\xae\x05\xbbR\xdd\x08\x9d4')
b'\xff\xf4'
65524
bytearray(b'\x81\xda\x1aH\x93\xce_\x9c')
b'\xf3\x01'
62209
bytearray(b'C\xfa\xd2\xa6\x8e?\xd0\x19')
b'\xe6\xc8'
59080
bytearray(b'\xad\x8b\xe4\x18K\xd6\x8ap')
b'\xf4\xec'
62700
bytearray(b'.=\x8f#\x8b\xfce\xc3')
b'5\xb5'
13749
bytearray(b'\x94\x9b\xbd\xe9\x9e\xb4\x1c\x81')
b'\x0c"'
3106
bytearray(b"\xeb\x84Lz\x91\x14

b'\xf3\xc0'
62400
bytearray(b'v\xda\x0c@\xcfg\xcco')
b'\xfe,'
65068
bytearray(b'QP\xa1\x99}\xffN\xfc')
b'\xfff'
65382
bytearray(b'\xab\xcb\xc7\xd8\x14\x93\x11\xe0')
b'\x01\x12'
274
bytearray(b'\xa9B\x1d*&\x04\xe9\xdf')
b'}z'
32122
bytearray(b'U76\xd6\xce;\xef\xcd')
b'\xf5\xe6'
62950
bytearray(b'\xccp`A\x90\x98B\xdb')
b'\xbc\x00'
48128
bytearray(b'\xa4\xc6\x0eQ\xb1\xc9x\xdf')
b'\nB'
2626
bytearray(b'}\xea\xee\xd0\x93\xa7S\xcc')
b'K\xec'
19436
bytearray(b' /\x0f\xbeW#\t\x18')
b'\xdd\xe4'
56804
bytearray(b'\xe9\xfeJ\x14\n\x86\x91\x10')
b'a\x07'
24839
bytearray(b'\x81\xd9zD\xc9\xd7\xcd\x0e')
b'\xc1"'
49442
bytearray(b'+\xfa\x91\xde\x84m\xbf?')
b'm\xe4'
28132
bytearray(b'\xd6\xc46\xfb\\\xe8\x04\x87')
b'V-'
22061
bytearray(b'\xe4\x1d\xcd\xc1r\xa3\x19\x12')
b'\xee\x9a'
61082
bytearray(b"]d(\x08E\x04\xea\'")
b'\x04p'
1136
bytearray(b'6*$\xc6\xb9dm\xf6')
b'\xe5\xf1'
58865
bytearray(b'%\x8d\xb8\x86AC\x94\xd3')
b'*\x7f'
10879
bytearray(b'2e\xc2\x94[\xe8\xcb\x00')
b'P\xa7'
20647
bytearray(b'\x99\x

b'\xa3\x9d'
41885
bytearray(b'\xaa\x08)\x1d\xcd\x9972')
b'z\xfc'
31484
bytearray(b'\xced\xbcr\xb5\x01xi')
b'\x10A'
4161
bytearray(b'\xc8\x9c\xddn\xf9\x01\x92>')
b'K\xe4'
19428
bytearray(b'\xd8\x87\xe6\x92\xabMe,')
b'&%'
9765
bytearray(b'\x9b^b\xd3@{\x06e')
b'\xe2@'
57920
bytearray(b'\x80\xc5&\x90<\xf64\x97')
b'\xce~'
52862
bytearray(b'^\xebf@Q!\xf4*')
b'~r'
32370
bytearray(b'\x1a\x8b\xfb)\x9e\x11B\xfe')
b'\xaf\x00'
44800
bytearray(b'\xb5\n\xf21\xe9\xfa\xe5\x0e')
b'Z`'
23136
bytearray(b'\xb0\xd6\x8b\xf4\x95\xca\xb5\x86')
b'\xfb0'
64304
bytearray(b'\xa9\xe6\x1f9\xf6)\xe4y')
b'\x80\x03'
32771
bytearray(b'\\\xbf\x01,.;\xd4\xfa')
b'\x8e\x7f'
36479
bytearray(b'c6\xfe}Ghx2')
b'\x8b\xff'
35839
bytearray(b'x\x10\xdau\xbb(\xfa\x1c')
b'\x00\x02'
2
bytearray(b'\x13\x8a\x8e\x12>\xcc\x8d\xfe')
b'\x86\xde'
34526
bytearray(b'0\x05\x84\x82\xedRO\xc5')
b'\xbf\xf4'
49140
bytearray(b'\x83\x083\xbbK\x91\x0cZ')
b'\x10\x13'
4115
bytearray(b'g\x12\xe3\xe60\x81\x8aM')
b'_\xec'
24556
bytearray(b'\x8d\x1b`X\x97$

b'\xc0\xf7'
49399
bytearray(b'v2\xb9\xa6\x11h\xf9B')
b'\xa7\xb9'
42937
bytearray(b'1~h7\x8d\x0c<\x90')
b'\xf6\xfa'
63226
bytearray(b'\\\xaa\xfc+\x96\x18\x1b6')
b'\xdf\xe7'
57319
bytearray(b'Y\xd6#\xbd6Z\xdfC')
b'\xb6\xc0'
46784
bytearray(b'\xf6p\x8c\xb3\x1fl+\x9f')
b',Z'
11354
bytearray(b'v(\x19\xe3\x94\x9e\x7f\xf0')
b'\xff\x00'
65280
bytearray(b'\xb2\xc6y\x9a\xd8\x94\xb7\xf1')
b'\xbfJ'
48970
bytearray(b'%:\xb5\xd8\xb2/\xcf\x06')
b'yA'
31041
bytearray(b'4\xd4\xdb\xb4v\xd8\xa6\xd3')
b'#P'
9040
bytearray(b'\xf6]\x8e)\xb6\xe1\xc5G')
b'\xdb\xfc'
56316
bytearray(b'qu\x04\xfam\xb1\x8e~')
b'\xad\x00'
44288
bytearray(b'\xa7*\xc2\xf1\xab\xd9\xed1')
b'\xb21'
45617
bytearray(b'\x86\xd7\xba\x01\xf8~O\xa4')
b'\x00\xc5'
197
bytearray(b't\xbf\x12-#L\xa2P')
b'\xd4\xf4'
54516
bytearray(b'Z\xbeNE\xbb\xe3wU')
b'\xff\xfe'
65534
bytearray(b'\xf2= \xd6/\xe3\xa9\xc9')
b'\xe3d'
58212
bytearray(b'x\xb6g\x88S!\x86\x01')
b'\xff\xd6'
65494
bytearray(b'rZ7\x1c\x9f\x914\xf2')
b'\xf6\xa2'
63138
bytearray(b'\x1c.\xd7

Now, lets save the output on a npz file.

In [122]:
# output list into npz file, save as directory with one item 'response'
print(type(responses))
out_filename = "../Responses/fpga0_resp0_50k_grad.npz"
np.savez(out_filename, response=responses)
print('Output File =', out_filename)

print("✔️ OK to continue!")

<class 'numpy.ndarray'>
Output File = ../Responses/fpga0_resp0_50k_grad.npz
✔️ OK to continue!


Re-run these functions to generate all 6 responses: 3 for each FPGA. Make sure to rename the output file adequatly to represent each varying file.